# Crossover Swath/Nadir

In [ ]:
import subprocess

import distributed

# Guessing installed cluster type
c = subprocess.run("qstat", capture_output=True, shell=True)

if c.returncode != 0:
    cluster_type = "slurm"
else:
    cluster_type = "sge"

In [ ]:
import numpy as np
from casys.readers import ScCollectionReader
from octantng.core.dask import DaskCluster

from casys import CasysPlot, Field, NadirData, PlotParams, SwathData

SwathData.enable_loginfo()

In [ ]:
dask_cluster = DaskCluster(cluster_type=cluster_type, jobs=(10, 10), memory=4)

dask_client = dask_cluster.client
dask_cluster.wait_for_workers(n_workers=3, timeout=600)

## Swath reader and container definition

Initializing the reader:

In [ ]:
collection_swath_path = "/data/OCTANT_NG/tests/ce_swot/zcollection/"

variables = [
    "cross_track_distance",
    "cycle_number",
    "latitude_nadir",
    "latitude",
    "longitude_nadir",
    "longitude",
    "pass_number",
    "time",
    "ssh_karin",
    "swh_karin",
]

reader_swath = ScCollectionReader(
    data_path=collection_swath_path,
    backend_kwargs={
        "cycle_numbers": 1,
        "pass_numbers": np.arange(2, 16, 2),
        "selected_variables": variables,
    },
    longitude="longitude",
    latitude="latitude",
    cycle_number="cycle_number",
    pass_number="pass_number",
    cross_track_distance="cross_track_distance",
)

Building the SwathData object:

In [ ]:
ad_swath = SwathData(source=reader_swath,)

## Nadir reader and container definition

Initializing the reader:

In [ ]:
collection_nadir_path = "/data/OCTANT_NG/tests/ce_swot/zcollection_nadir"

reader_nadir = ScCollectionReader(
    data_path=collection_nadir_path,
    backend_kwargs={"cycle_numbers": 1, "pass_numbers": np.arange(15, 30, 2)},
)

Building the NadirData object:

In [ ]:
ad_nadir = NadirData(
    source=reader_nadir,
    time="data_01.time",
    longitude="data_01.longitude",
    latitude="data_01.latitude",
    cycle_number="cycle_number",
    pass_number="pass_number",
)

## Definition of the crossover diagnostic

Using the [add_crossover_stat](../generated/casys.computation.rst#casys.computation.SwathData.add_crossover_stat) method:

In [ ]:
ad_swath.add_crossover_stat(
    name="SWH crossover",
    field=Field(name="swh_karin", source_aux="data_01.ku.swh_ocean"),
    data=ad_nadir,
    stats=["mean"],
    max_time_difference="5000D",
    temporal_stats_freq=["1h"],
    temporal_freq_kwargs={"normalize": True},
    diamond_reduction="mean",
    diamond_relocation=False,
)

In [ ]:
ad_swath.add_crossover_stat(
    name="SWH crossover no reduction",
    field=Field(name="swh_karin", source_aux="data_01.ku.swh_ocean"),
    data=ad_nadir,
    stats=["mean"],
    max_time_difference="5000D",
    temporal_stats_freq=["1h"],
    temporal_freq_kwargs={"normalize": True},
    diamond_reduction="none",
    diamond_relocation=False,
)

## Computation

In [ ]:
ad_swath.compute_dask()

## Plot

In [ ]:
plot_time_delta = CasysPlot(
    data=ad_swath,
    data_name="SWH crossover",
    delta="time",
    plot_params=PlotParams(grid=True, marker_size=12),
)
plot_time_delta.show()

In [ ]:
plot_time_delta = CasysPlot(
    data=ad_swath,
    data_name="SWH crossover",
    delta="time",
    plot_params=PlotParams(
        grid=True,
        marker_size=12,
        x_limits=(90, 150),
        y_limits=(-55, -85),
    ),
)
plot_time_delta.show()

Disabling the crossover points reduction:

In [ ]:
plot_time_delta_no_reduction = CasysPlot(
    data=ad_swath,
    data_name="SWH crossover no reduction",
    delta="time",
    plot_params=PlotParams(grid=True),
)
plot_time_delta_no_reduction.show()

In [ ]:
plot_time_delta_no_reduction = CasysPlot(
    data=ad_swath,
    data_name="SWH crossover no reduction",
    delta="time",
    plot_params=PlotParams(
        grid=True,        
        x_limits=(90, 150),
        y_limits=(-55, -85),
    )
)
plot_time_delta_no_reduction.show()

## Extracting results from diagnostic

Extract the result from the SwathData object specifying the diagnostic name:

In [ ]:
swh_diag = ad_swath.get_diagnostic("SWH crossover")

The parameters passed to the diagnostic can be accessed through attributes.  
The various results are available via the `results` attribute. The different type of diagnostic are:

- data: xarray dataset containing crossover difference, geobox binning and temporal binning results
- delta: difference results at crossover diamond points (reduced to crossover nadir points if the parameter `diamond_reduction` was filled)

In [ ]:
swh_diag.results.delta

- geo_box: geographic binning results
- temporal: along time binning results
- locations: structured array containing crossovers details (lon, lat, cycle_numbers, pass_numbers)

In [ ]:
swh_diag.results.locations

In [ ]:
dask_cluster.close()

To learn more about crossovers definition, please visit this documentation [page](../diagnostics/crossovers_stat_swath.rst).